In [1]:
import os
from glob import glob
from pymystem3 import Mystem
import pandas as pd
import json
import pickle

In [2]:
pp = os.getcwd()
PATH_DD = pp.split('group_mlada')[0] + 'group_mlada/'

In [3]:
train_path = f'{PATH_DD}/data/train/train.parquet'
train = pd.read_parquet(train_path, engine='pyarrow')

In [4]:
train.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1168516 entries, 0 to 1168515
Data columns (total 3 columns):
 #   Column      Non-Null Count    Dtype
---  ------      --------------    -----
 0   variantid1  1168516 non-null  int64
 1   variantid2  1168516 non-null  int64
 2   target      1168516 non-null  int64
dtypes: int64(3)
memory usage: 26.7 MB


In [5]:
train.head(10)

variantid1  variantid2  target
0  1447875869  1447872068       1
1  1176231201   284733670       1
2   658617865   549848659       0
3   719320625   719370486       1
4  1067645658   949954740       0
5   504121134   304997246       0
6   690909146  1044397832       1
7   691943502   691868704       0
8   479881093   256110461       1
9   905617449   905617985       0

In [6]:
attributes_path = f'{PATH_DD}/data/train/attributes.parquet'
attributes = pd.read_parquet(attributes_path, engine='pyarrow')

In [7]:
attributes.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2252569 entries, 0 to 2252568
Data columns (total 3 columns):
 #   Column                             Dtype 
---  ------                             ----- 
 0   variantid                          int64 
 1   categories                         object
 2   characteristic_attributes_mapping  object
dtypes: int64(1), object(2)
memory usage: 51.6+ MB


In [8]:
attributes.head(10)

variantid                                         categories  \
0   47920382  {"1": "EPG", "2": "Детские товары", "3": "Игру...   
1   49801845  {"1": "EPG", "2": "Хобби и творчество", "3": "...   
2   49853444  {"1": "EPG", "2": "Хобби и творчество", "3": "...   
3   49893028  {"1": "EPG", "2": "Хобби и творчество", "3": "...   
4   49987483  {"1": "EPG", "2": "Хобби и творчество", "3": "...   
5   49995691  {"1": "EPG", "2": "Хобби и творчество", "3": "...   
6   50101275  {"1": "EPG", "2": "Хобби и творчество", "3": "...   
7   50373843  {"1": "EPG", "2": "Хобби и творчество", "3": "...   
8   51158084  {"1": "EPG", "2": "Дом и сад", "3": "Подушки, ...   
9   51252362  {"1": "EPG", "2": "Дом и сад", "3": "Столовая ...   

                   characteristic_attributes_mapping  
0  {"Цвет товара": ["бежевый", "светло-розовый"],...  
1  {"Количество в упаковке, шт": ["1"], "Бренд": ...  
2  {"Бренд": ["Vervaco"], "Тип": ["Набор для выши...  
3  {"Цвет товара": ["серый"], "Ширина, см": ["0.8...  
4  {"Цвет товара": ["разноцветный"], "Название цв...  
5  {"Тип": ["Настольная игра"], "Страна-изготовит...  
6  {"Цвет товара": ["зеленый", "прозрачный"], "На...  
7  {"Цвет товара": ["синий"], "Количество в упако...  
8  {"Артикул": ["ОШО 4 - 3 Л"], "Тип": ["Одеяло"]...  
9  {"Артикул": ["991"], "Комплектация": ["- чайни...

In [9]:
print(len(attributes))

2252569


#### Составление описания объекта
<br>
Категории<br>

Начинаем со второй <br>
категория 2 под литерой a + номер от 0 до 23<br>
категория 3 под литерой b + номер от 0 до 582<br>
категория 4 под литерой c + номер от 0 до 3685<br>
<br>
характеристики под литерой d + номер от 0 до 6015<br><br>
Пример описания объекта<br>

a18 b320 c1643 d12 d67 d2845 

На первом  этапе обучение на описании только кодами ктегорий и характкристик <br>
На втором  этапе обучение на первом описании + все слова из характеристик<br>
На третьем этапе обучение на первом описании + все слова из характеристик + все цифры из характеристик<br>



In [10]:
def get_dict(name_f:str) ->dict:
    '''
    Получение словаря из файла
    '''
    r_d= {}
    with open(PATH_DD + name_f, 'r') as f:
        for line in f:
            line_l = line.strip().split(';')
            r_d[line_l[0]] = line_l[2]
    return r_d

In [11]:
d_characteristic = get_dict('data/characteristic.csv')
d_categories2 = get_dict('data/stat_categories2.csv')
d_categories3 = get_dict('data/stat_categories3.csv')
d_categories4 = get_dict('data/stat_categories4.csv')
d_all = {'d2': d_categories2,
         'd3': d_categories3,
         'd4': d_categories4,
         'dc': d_characteristic} 

In [13]:
def print_obj(desc_all_obj, nn: int):
    k = 0
    for key in desc_all_obj:
        if k == nn:
                print(key, desc_all_obj[key], sep=' ==> ')
                break
        k += 1

    

In [14]:
desc_all_obj ={}
with open(PATH_DD + 'data/all_obj.csv', 'r') as f:
    for line in f:
        line_l = line.strip().split(';')
        desc_all_obj[line_l[0].strip()] = line_l[1]
print(len(desc_all_obj))

2252569


In [15]:
print_obj(desc_all_obj, 999)
print_obj(desc_all_obj, 1000)
print_obj(desc_all_obj, 1001)

628056916 ==> b9 c52 d691 e978 e494 e305 e423 e239 e230 e297 e580 e257 e19 e9 e518 e4 e14 e255 e0 e1 e452 e298 e405 e380 e68 e700 e394 e463 e638 e241 e363 e236 e359 e419 e849 e412 e672 e268 e783 e244 e273 e289 e238 e252 e616 e2343 e2 e418 e443 e685 e403 e3 e6 e275 e69 e295
628105125 ==> b4 c252 d1757 e4 e14 e100 e27 e0 e1 e63 e44 e182 e1780 e3 e1799 e6 e151 e2 e145 e5
628139361 ==> b4 c2 d583 e8 e27 e0 e2


In [18]:
label = []
X=[]
Y=[]
for row in train.iterrows():
    # print(row)
    # print(row[1]['variantid1'])
    # print(row[1]['variantid2'])
    # print(row[1]['target'])
    label.append(row[0])
    if str(row[1]['variantid1']).strip() in desc_all_obj and str(row[1]['variantid2']).strip() in desc_all_obj:
        # print(desc_all_obj[row[1]['variantid1']])
        X.append(
            desc_all_obj[str(row[1]['variantid1']).strip()] + ' ' +
            desc_all_obj[str(row[1]['variantid2']).strip()])
        Y.append(row[1]['target'])
    # else:
    #     print('not found')
    #break
print(len(X))

1168516


In [19]:
X[100]

'b10 c251 d747 e39 e18 e0 e1 e7 e20 e56 e16 e3 e6 e22 e2 e77 e10 e5 e41 e1385 e9 b10 c251 d747 e39 e896 e0 e1 e7 e20 e16 e3 e6 e22 e2 e77 e10 e5 e1385 e9 e302'

In [20]:
Y[100]

0

In [19]:
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.pipeline import Pipeline
from sklearn.model_selection import train_test_split
from sklearn.naive_bayes import MultinomialNB
from sklearn.metrics import accuracy_score, precision_score, recall_score, roc_auc_score
from sklearn.ensemble import RandomForestClassifier

In [ ]:
def train_classifier(data, labels):
    vectorizer = TfidfVectorizer()
    X = vectorizer.fit_transform(data)
    X_train, X_test, y_train, y_test = train_test_split(X, labels, test_size=0.2, random_state=42)
    
    random_forest_model = RandomForestClassifier(n_estimators=5, random_state=42, n_jobs=-1)
    random_forest_model.fit(X_train, y_train)
    
    y_pred_rf = random_forest_model.predict(X_test)
    print("Random Forest Accuracy:", accuracy_score(y_test, y_pred_rf))
    precision = precision_score(y_test, y_pred_rf)
    recall = recall_score(y_test, y_pred_rf)
    auc = roc_auc_score(y_test, y_pred_rf)
    # print(f'Accuracy: {accuracy:.4f}')
    print(f'Precision: {precision:.4f}')
    print(f'Recall: {recall:.4f}')
    print(f'AUC: {auc:.4f}')
    
    return random_forest_model, vectorizer

In [23]:
random_forest_model, vectorizer = train_classifier(X, Y)

Random Forest Accuracy: 0.7470133159894567
Precision: 0.7456
Recall: 0.7189
AUC: 0.7460


In [61]:
X_train, X_test, y_train, y_test = train_test_split(X, Y, test_size=0.10, random_state=42)
vectorizer = CountVectorizer()
X_train_counts = vectorizer.fit_transform(X_train)

In [62]:
tfidf_transformer = TfidfTransformer()
X_train_tfidf = tfidf_transformer.fit_transform(X_train_counts)

In [63]:
# Метод наивный Байес
clf = MultinomialNB().fit(X_train_tfidf, y_train)

In [64]:
X_test_new = vectorizer.transform(X_test)
#print(X_test_new.shape)
X_new_tfidf = tfidf_transformer.transform(X_test_new)
predicted = clf.predict(X_new_tfidf)

In [65]:
kk = 0
for doc, category in zip(y_test, predicted):
    print(doc, category)
    if doc == category: kk +=1
        
print('model ', kk/len(y_test))

1 1
0 1
1 1
0 0
1 1
1 0
1 1
1 1
1 1
1 1
1 0
1 1
0 1
1 1
0 1
0 1
1 1
0 0
0 0
0 1
0 1
0 0
1 1
0 1
0 0
0 0
0 1
1 1
1 1
0 0
0 1
0 1
0 1
1 1
0 0
1 1
1 0
0 0
0 0
0 0
0 0
0 1
1 1
1 1
1 1
1 1
1 1
0 1
0 0
0 0
0 0
0 0
1 0
0 0
0 1
1 1
1 1
0 0
0 0
0 0
0 0
0 0
1 0
1 1
1 1
0 1
0 0
1 0
0 0
0 0
0 0
0 0
0 0
0 0
0 1
1 0
1 0
0 0
1 1
1 1
1 1
1 1
1 0
1 1
0 0
0 0
0 0
1 1
0 0
0 1
0 1
1 1
0 0
1 0
1 1
0 0
0 0
0 0
1 1
1 1
0 0
0 0
0 0
0 0
0 0
0 0
0 0
1 1
0 1
0 0
0 1
0 0
0 0
1 1
0 1
0 1
0 1
0 1
0 0
0 0
1 1
1 1
1 0
0 1
1 1
0 0
0 1
0 0
1 1
1 1
0 0
0 1
0 1
0 0
0 1
0 0
1 1
1 0
1 1
1 0
0 1
1 1
0 1
0 0
0 1
1 1
0 0
0 1
0 1
1 1
1 1
0 1
0 0
1 1
0 0
0 0
0 0
1 0
0 0
1 1
1 0
0 0
1 1
1 0
0 0
0 1
1 1
0 1
1 0
0 1
0 1
1 0
1 1
1 1
1 0
1 1
1 1
0 0
0 0
0 0
0 1
0 0
1 0
0 1
0 0
0 0
0 1
0 0
1 0
1 0
0 1
1 0
0 0
1 1
1 0
0 0
1 1
1 0
0 1
0 1
0 0
1 0
0 0
0 0
0 0
0 0
1 0
0 1
0 1
1 1
1 1
0 0
0 0
1 0
1 1
0 0
0 0
1 1
0 1
1 1
1 1
1 1
0 0
0 1
0 1
0 0
0 1
0 0
1 1
0 0
0 0
0 1
0 0
0 0
1 1
1 0
0 0
1 1
0 0
0 0
0 0
0 0
0 0
0 0
1 1
0 0
0 1
0 0
1 1
1 1


In [67]:
# Вывод метрик
accuracy = accuracy_score(y_test, predicted)
precision = precision_score(y_test, predicted)
recall = recall_score(y_test, predicted)
auc = roc_auc_score(y_test, predicted)

print(f'Accuracy: {accuracy:.4f}')
print(f'Precision: {precision:.4f}')
print(f'Recall: {recall:.4f}')
print(f'AUC: {auc:.4f}')

Accuracy: 0.6741
Precision: 0.6512
Recall: 0.6979
AUC: 0.6750


#### Обработка текстов атрибутов

In [20]:
from pymystem3 import Mystem
import pickle
m = Mystem()

In [21]:
def get_lem_words(ss: str) -> list:
    '''
    Получение слов из строки
    '''
    ww= []
    ss = ss.strip().lower()
    ddel = ['*', ',', '-', '/', '%', ';', ')', '+', '.', '..', ':']
    for i in ddel:
        ss = ss.replace(i, ' ')
    ssl = ss.split()
    for word in ssl:
        # print(word)
        if not word.isdigit():
            lemmas = m.lemmatize(word)
            ww.append(lemmas[0])
    return ww
    

In [18]:
def get_all_text_catgory3(d_all, row, desc_all_text_cat3):
    '''
    Получение описание объекта в кодах-словах
    '''
    all_word = []
    dd = json.loads(row['categories'])
    # print(desc_all_text_cat4)
    # print(d_all['d4'][dd['4']])
    #[d_all)
    #      ['d4']])
    # print(desc_all_text_cat4[d_all['d4'][dd['4']]])
    # #print(row['characteristic_attributes_mapping'])
    if d_all['d3'][dd['3']] not in desc_all_text_cat3:
        desc_all_text_cat3[d_all['d3'][dd['3']]] = []
    ar = json.loads(row['characteristic_attributes_mapping'])
    #print(ar)
    for key in ar:
        if isinstance(ar[key], list):
            # print(key)
            for ww in ar[key]:
                
                all_word = all_word + get_lem_words(ww)
            # print()
    desc_all_text_cat3[d_all['d3'][dd['3']]] = desc_all_text_cat3[d_all['d3'][dd['3']]] + all_word
    return desc_all_text_cat3

In [22]:
desc_all_text_cat3 ={}
kk = 0
for i in range(0, len(attributes)):
    # print(attributes.iloc[i])
    desc_all_text_cat3 = get_all_text_catgory3(d_all, attributes.iloc[i], desc_all_text_cat3)
    print(desc_all_text_cat3)
    # if kk == 3:
    #     break
    kk += 1
    if kk%100000 == 0:
        print(kk)

print(len(desc_all_text_cat3))
# print(desc_all_text_cat4)

{'c8': ['бежевый', 'светло', 'розовый', 'унисекс', 'funny', 'ducks', 'игрушка', 'для', 'ванна', 'китай', 'воображение', 'кругозор', 'моторика', 'от', 'год', 'пвх', 'пластизоль', 'до', 'год']}
{'c8': ['бежевый', 'светло', 'розовый', 'унисекс', 'funny', 'ducks', 'игрушка', 'для', 'ванна', 'китай', 'воображение', 'кругозор', 'моторика', 'от', 'год', 'пвх', 'пластизоль', 'до', 'год'], 'c16': ['нет', 'бренд', 'страз', 'акрил']}
{'c8': ['бежевый', 'светло', 'розовый', 'унисекс', 'funny', 'ducks', 'игрушка', 'для', 'ванна', 'китай', 'воображение', 'кругозор', 'моторика', 'от', 'год', 'пвх', 'пластизоль', 'до', 'год'], 'c16': ['нет', 'бренд', 'страз', 'акрил'], 'c15': ['vervaco', 'набор', 'для', 'вышивание', 'бельгия', 'акрил', 'бумага', 'канва', 'металл', 'хлопок', 'простой', 'крест', 'от', 'год', 'х']}
{'c8': ['бежевый', 'светло', 'розовый', 'унисекс', 'funny', 'ducks', 'игрушка', 'для', 'ванна', 'китай', 'воображение', 'кругозор', 'моторика', 'от', 'год', 'пвх', 'пластизоль', 'до', 'год'], 

In [60]:
# with open(PATH_DD + 'data/desc_all_text_cat4.pickle', 'bw') as f:
#     pickle.dump(desc_all_text_cat4, f)
with open(PATH_DD + 'data/desc_all_text_cat4.pickle', 'br') as f:
    desc_all_text_cat4 = pickle.load(f)

In [63]:
sets_desc_all_text_cat4 ={}
for key in desc_all_text_cat4:
    if key not in sets_desc_all_text_cat4:
        sets_desc_all_text_cat4[key] = set(desc_all_text_cat4[key])
    # print(key, len(desc_all_text_cat4[key]))
    # print(len(set(desc_all_text_cat4[key])))
    # break

In [66]:
# with open(PATH_DD + 'data/sets_desc_all_text_cat4.pickle', 'bw') as f:
#     pickle.dump(sets_desc_all_text_cat4, f)
with open(PATH_DD + 'data/sets_desc_all_text_cat4.pickle', 'br') as f:
    sets_desc_all_text_cat4= pickle.load(f)

In [68]:
com_list_words = []
for key in sets_desc_all_text_cat4:
    com_list_words.append(sets_desc_all_text_cat4[key])
print(len(com_list_words))

3686


In [72]:
int_result = set.intersection(*com_list_words)
len(int_result)

0

In [75]:
uni_result = set.union(*com_list_words)
len(uni_result)
    

992706

In [78]:
# set_com_words = set()
# for key1 in sets_desc_all_text_cat4:
#     for key2 in sets_desc_all_text_cat4:
#         if key1 != key2:
#             int_res = sets_desc_all_text_cat4[key1].intersection(sets_desc_all_text_cat4[key2])
#             if len(int_res) > 0:
#                 for word in int_res:
#                     set_com_words.add(word)
# print(len(set_com_words))

154880


In [79]:
set_com_words

{'феррара',
 '247мм',
 '472pg',
 'фукоидан',
 'ная',
 'sandokkaebi',
 '242x166x4',
 '40x110',
 'эвалдс',
 'костова',
 '26х14х8',
 'сюрприз',
 'f5c',
 'бракованный',
 'yoshatoys',
 'голуб',
 'z510',
 'rapid',
 'beer',
 '19х19х4',
 'напоминать',
 'bd1422',
 '320h',
 '230x165x3',
 'amdsa113l',
 'выдра',
 'эластан1',
 'x413fa',
 'bc50617',
 'глазунья',
 'skif',
 'трость',
 'электронасос',
 '90х210',
 'f125nc',
 '290x205x5',
 'ванночка',
 'койдль',
 'серобежевый',
 '950х470',
 'трамп',
 'ремиссия',
 'рин',
 '850х600',
 'сальгари',
 'minx',
 'aaaline',
 'vm',
 'изононила',
 'поильник',
 '5х9х28',
 'glucosyl',
 'корректироваться',
 '40x47',
 'zak5990',
 'ip54',
 'lipai',
 'росмэн',
 'mecha',
 'боэ',
 'эйлин',
 '728',
 'подозревать',
 '60f',
 'зародышевый',
 '500х650',
 'carmega',
 'bc8378',
 'm015',
 '50х50х150',
 'эндорфин',
 'разрешаться',
 'деменкова',
 'докучаев',
 'вышеперечисленный',
 'floridis',
 'хеллоуин',
 'метилировать',
 'люверс',
 '1000х',
 'v60',
 'пис',
 'sound',
 'небыков',
 '

In [80]:
# with open(PATH_DD + 'data/set_com_words.pickle', 'bw') as f:
#     pickle.dump(set_com_words, f)
with open(PATH_DD + 'data/set_com_words.pickle', 'br') as f:
    set_com_words = pickle.load(f)

In [86]:
def get_lem_words_two(ss: str) -> list:
    '''
    Получение слов из строки
    '''
    ww= []
    ss = ss.strip().lower()
    ddel = ['*', ',', '-', '/', '%', ';', ')', '+', '.', '..', ':']
    for i in ddel:
        ss = ss.replace(i, ' ')
    ssl = ss.split()
    for word in ssl:
        # print(word)
        if not word.isdigit():
            lemmas = m.lemmatize(word)
            if not lemmas[0] in set_com_words:
                ww.append(lemmas[0])
    return ww

In [82]:
def get_sequence_v(row):
    '''
    Получение предложения описания объекта в кодах-словах
    '''
    all_word = []
    ar = json.loads(row['characteristic_attributes_mapping'])
    #print(ar)
    for key in ar:
        if isinstance(ar[key], list):
            # print(key)
            for ww in ar[key]:
                
                all_word = all_word + get_lem_words_two(ww)
            # print()
    return ' '.join(all_word)

In [89]:
X_words = []
pusto = 0
Y_var = []
k = 0
for i in range(0, len(attributes)):
    v = attributes.iloc[i]['variantid']
    Y_var.append(str(v).strip())
    sequence_v = get_sequence_v(attributes.iloc[i])
    if sequence_v:
        X_words.append(sequence_v)
    else:
        X_words.append(['pusto'])
        pusto += 1
    # if k == 10:
    #     break
    # k += 1
print(len(X_words))
# print(X_words)

2252569


In [26]:
with open(PATH_DD + 'data/X_words.pickle', 'br') as f:
    X_words = pickle.load(f)
with open(PATH_DD + 'data/Y_var.pickle', 'br') as f:
    Y_var = pickle.load(f)

In [29]:
X_words[1000]

'maket2809 zuz'

In [27]:
desc_all_obj2= {}
for key, sens in zip(Y_var, X_words):
    desc_all_obj2[key] = sens
desc_all_obj2

{'47920382': ['pusto'],
 '49801845': ['pusto'],
 '49853444': 'vervaco',
 '49893028': ['pusto'],
 '49987483': ['pusto'],
 '49995691': ['pusto'],
 '50101275': ['pusto'],
 '50373843': ['pusto'],
 '51158084': ['pusto'],
 '51252362': 'гунф kamjove',
 '51435411': ['pusto'],
 '51808863': ['pusto'],
 '51818622': ['pusto'],
 '51822217': '920г',
 '51835261': ['pusto'],
 '51839960': ['pusto'],
 '53551326': '2250п206532 185x215',
 '53597978': ['pusto'],
 '53780071': ['pusto'],
 '53831190': 'птг',
 '54156768': ['pusto'],
 '54195604': ['pusto'],
 '54231951': ['pusto'],
 '54293431': ['pusto'],
 '54465093': ['pusto'],
 '54503110': ['pusto'],
 '54519114': ['pusto'],
 '54645798': '370x470',
 '55077096': ['pusto'],
 '55346949': ['pusto'],
 '55451546': ['pusto'],
 '55826147': ['pusto'],
 '56182724': ['pusto'],
 '56372256': '27х21х8 1100х725х5',
 '56391801': 'aquamenu',
 '56451125': ['pusto'],
 '57462509': ['pusto'],
 '57621083': 'hydralphatine aldavine микрокапиллярный глазамичерез литцея',
 '57969968': '

In [28]:
label = []
X2=[]
Y2=[]
for row in train.iterrows():
    # print(row)
    # print(row[1]['variantid1'])
    # print(row[1]['variantid2'])
    # print(row[1]['target'])
    label.append(row[0])
    if str(row[1]['variantid1']).strip() in desc_all_obj2 and str(row[1]['variantid2']).strip() in desc_all_obj2:
        
        # print(desc_all_obj[row[1]['variantid1']])
        a = ''
        b = ''
        if type(desc_all_obj2[str(row[1]['variantid1'])]) == list:
            a = 'pusto'
        else: a = desc_all_obj2[str(row[1]['variantid1']).strip()]
        if type(desc_all_obj2[str(row[1]['variantid2'])]) == list:
            b = 'pusto'
        else: b = desc_all_obj2[str(row[1]['variantid2']).strip()]
    X2.append(a + ' ' + b)
    Y2.append(row[1]['target'])
    # else:
    #     print('not found')
    #break
print(len(X2))

1168516


In [30]:
X2[1000]

'pusto pusto'

In [31]:
random_forest_model2, vectorizer2 = train_classifier(X2, Y2)

: 

: 

In [ ]:
X_words

In [90]:
# with open(PATH_DD + 'data/X_words.pickle', 'bw') as f:
#     pickle.dump(X_words, f)
# with open(PATH_DD + 'data/Y_var.pickle', 'bw') as f:
#     pickle.dump(Y_var, f)

In [98]:
X_train2, X_test2, y_train2, y_test2 = train_test_split(X2, Y2, test_size=0.20, random_state=42)
vectorizer = CountVectorizer()
X_train_counts2 = vectorizer.fit_transform(X_train2)

In [99]:
tfidf_transformer = TfidfTransformer()
X_train_tfidf2 = tfidf_transformer.fit_transform(X_train_counts2)

In [101]:
# Метод наивный Байес
clf = MultinomialNB().fit(X_train_tfidf2, y_train2)

In [102]:
X_test_new2 = vectorizer.transform(X_test2)
#print(X_test_new.shape)
X_new_tfidf2 = tfidf_transformer.transform(X_test_new2)
predicted2 = clf.predict(X_new_tfidf2)

In [104]:
kk = 0
for doc, category in zip(y_test2, predicted2):
    print(doc, category)
    if doc == category: kk +=1
        
print('model ', kk/len(y_test2))

1 1
0 0
1 1
0 0
1 0
1 0
1 0
1 0
1 0
1 1
1 0
1 0
0 1
1 0
0 0
0 0
1 0
0 0
0 0
0 0
0 0
0 0
1 0
0 0
0 1
0 0
0 0
1 0
1 0
0 0
0 0
0 0
0 0
1 0
0 0
1 0
1 0
0 0
0 0
0 0
0 0
0 0
1 0
1 0
1 0
1 0
1 1
0 0
0 1
0 0
0 0
0 0
1 0
0 0
0 0
1 1
1 0
0 0
0 0
0 0
0 0
0 0
1 0
1 0
1 0
0 0
0 0
1 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
1 0
1 0
0 0
1 1
1 0
1 0
1 0
1 1
1 0
0 0
0 0
0 0
1 1
0 0
0 0
0 1
1 0
0 0
1 0
1 0
0 0
0 0
0 0
1 0
1 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
1 0
0 0
0 0
0 0
0 0
0 0
1 0
0 0
0 0
0 0
0 0
0 0
0 0
1 0
1 0
1 0
0 1
1 0
0 0
0 0
0 0
1 1
1 0
0 0
0 0
0 0
0 0
0 0
0 0
1 0
1 0
1 0
1 1
0 0
1 0
0 0
0 0
0 0
1 0
0 0
0 0
0 1
1 1
1 0
0 1
0 0
1 0
0 0
0 0
0 0
1 0
0 0
1 1
1 0
0 0
1 0
1 0
0 1
0 0
1 0
0 0
1 1
0 0
0 0
1 1
1 0
1 0
1 0
1 0
1 1
0 0
0 1
0 0
0 0
0 0
1 1
0 1
0 0
0 0
0 0
0 0
1 0
1 1
0 0
1 0
0 0
1 0
1 0
0 0
1 0
1 0
0 1
0 0
0 0
1 0
0 0
0 0
0 0
0 0
1 0
0 0
0 0
1 0
1 1
0 0
0 0
1 0
1 0
0 0
0 0
1 1
0 1
1 0
1 0
1 0
0 0
0 0
0 0
0 0
0 0
0 0
1 0
0 0
0 0
0 0
0 1
0 0
1 0
1 0
0 0
1 0
0 0
0 0
0 0
0 0
0 0
0 0
1 0
0 0
0 0
0 0
1 0
1 0


In [105]:
# Вывод метрик
accuracy2 = accuracy_score(y_test2, predicted2)
precision2 = precision_score(y_test2, predicted2)
recall2 = recall_score(y_test2, predicted2)
auc2 = roc_auc_score(y_test2, predicted2)

print(f'Accuracy: {accuracy2:.4f}')
print(f'Precision: {precision2:.4f}')
print(f'Recall: {recall2:.4f}')
print(f'AUC: {auc2:.4f}')

Accuracy: 0.5845
Precision: 0.7720
Recall: 0.1922
AUC: 0.5698


In [108]:
label3 = []
X3=[]
Y3=[]
for row in train.iterrows():
    # print(row)
    # print(row[1]['variantid1'])
    # print(row[1]['variantid2'])
    # print(row[1]['target'])
    label.append(row[0])
    if str(row[1]['variantid1']).strip() in desc_all_obj and str(row[1]['variantid2']).strip() in desc_all_obj:
        # print(desc_all_obj[row[1]['variantid1']])
        a = ''
        b = ''
        if type(desc_all_obj2[str(row[1]['variantid1'])]) == list:
            a = 'pusto'
        else: a = desc_all_obj2[str(row[1]['variantid1']).strip()]
        if type(desc_all_obj2[str(row[1]['variantid2'])]) == list:
            b = 'pusto'
        else: b = desc_all_obj2[str(row[1]['variantid2']).strip()]
        X3.append(
            desc_all_obj[str(row[1]['variantid1']).strip()] + ' ' + a +
            desc_all_obj[str(row[1]['variantid2']).strip()] + ' ' + b)
        Y3.append(row[1]['target'])
    # else:
    #     print('not found')
    #break
print(len(X3))

1168516


In [109]:
X_train3, X_test3, y_train3, y_test3 = train_test_split(X3, Y3, test_size=0.20, random_state=42)
vectorizer3 = CountVectorizer()
X_train_counts3 = vectorizer3.fit_transform(X_train3)

In [110]:
tfidf_transformer3 = TfidfTransformer()
X_train_tfidf3 = tfidf_transformer3.fit_transform(X_train_counts3)

In [111]:
# Метод наивный Байес
clf = MultinomialNB().fit(X_train_tfidf3, y_train3)

In [113]:
X_test_new3 = vectorizer3.transform(X_test3)
#print(X_test_new.shape)
X_new_tfidf3 = tfidf_transformer3.transform(X_test_new3)
predicted3 = clf.predict(X_new_tfidf3)

In [114]:
kk = 0
for doc, category in zip(y_test3, predicted3):
    print(doc, category)
    if doc == category: kk +=1
        
print('model ', kk/len(y_test3))

1 1
0 1
1 1
0 0
1 1
1 0
1 1
1 1
1 1
1 1
1 0
1 1
0 1
1 1
0 1
0 1
1 1
0 0
0 0
0 1
0 1
0 0
1 1
0 1
0 0
0 0
0 0
1 1
1 1
0 0
0 1
0 1
0 1
1 1
0 0
1 1
1 0
0 0
0 0
0 0
0 0
0 1
1 1
1 1
1 1
1 1
1 1
0 1
0 0
0 0
0 0
0 0
1 0
0 0
0 1
1 1
1 1
0 0
0 0
0 0
0 0
0 0
1 0
1 1
1 1
0 1
0 0
1 0
0 0
0 0
0 0
0 0
0 0
0 0
0 0
1 0
1 0
0 0
1 1
1 1
1 1
1 1
1 0
1 1
0 0
0 0
0 0
1 1
0 0
0 1
0 1
1 1
0 0
1 0
1 1
0 0
0 0
0 0
1 1
1 1
0 0
0 0
0 0
0 0
0 0
0 0
0 0
1 1
0 0
0 0
0 1
0 0
0 0
1 1
0 1
0 1
0 1
0 1
0 0
0 0
1 1
1 1
1 0
0 1
1 1
0 0
0 1
0 0
1 1
1 1
0 0
0 1
0 1
0 0
0 1
0 0
1 1
1 0
1 1
1 0
0 1
1 1
0 1
0 0
0 1
1 1
0 0
0 1
0 1
1 1
1 1
0 1
0 0
1 1
0 0
0 0
0 0
1 0
0 0
1 1
1 0
0 0
1 1
1 0
0 0
0 1
1 1
0 1
1 1
0 1
0 1
1 0
1 1
1 1
1 0
1 1
1 1
0 0
0 0
0 0
0 1
0 0
1 0
0 1
0 0
0 0
0 0
0 0
1 0
1 0
0 1
1 0
0 0
1 1
1 0
0 0
1 1
1 0
0 1
0 1
0 0
1 0
0 0
0 0
0 0
0 0
1 0
0 1
0 1
1 1
1 1
0 0
0 0
1 0
1 1
0 0
0 0
1 1
0 1
1 1
1 1
1 1
0 0
0 1
0 1
0 0
0 1
0 0
1 1
0 0
0 0
0 1
0 1
0 0
1 1
1 0
0 0
1 1
0 0
0 0
0 0
0 0
0 0
0 0
1 1
0 0
0 1
0 0
1 1
1 1


In [115]:
# Вывод метрик
accuracy3 = accuracy_score(y_test3, predicted3)
precision3 = precision_score(y_test3, predicted3)
recall3 = recall_score(y_test3, predicted3)
auc3 = roc_auc_score(y_test3, predicted3)

print(f'Accuracy: {accuracy3:.4f}')
print(f'Precision: {precision3:.4f}')
print(f'Recall: {recall3:.4f}')
print(f'AUC: {auc3:.4f}')

Accuracy: 0.6804
Precision: 0.6603
Recall: 0.6901
AUC: 0.6807
